## 5. モンテカルロシミュレーション

### まとめと演習

#### Lennard-Jones流体のシミュレーション

##### Lennard-Jones model

<img src="fig/LJ.png">

- 粒子対 $i,j$ 間のポテンシャルエネルギー関数
$$
\phi(r_{ij})=4\epsilon\left[\left(\frac{\sigma}{r_{ij}}\right)^{12}-\left(\frac{\sigma}{r_{ij}}\right)^{6}\right],\ \ \ \ r_{ij}=\left|{\bf r}_{i}-{\bf r}_{j}\right|
$$
 右辺第一項は近距離での粒子の反発を表し，第二項は 粒子間の引力を表す．Lennard-Jones model はアルゴンなど希ガスの性質を比較的よく再現し，与えられた熱力学状態（粒子数 $N$，温度 $T$，体積 $V=\rho N$）のもとで気体・液体・固体の３相（あるいはそれらの共存状態）をとることが出来る．

- 系全体のポテンシャルエネルギー
$$
E_p=\sum_{i=2}^{N}\sum_{j=1}^{i-1}\phi(r_{ij})
$$

##### シミュレーション条件
- カノニカルアンサンブル（$NVT$一定）
- 粒子数 $N=108$ 個
- メトロポリスの方法でカノニカルアンサンブルに基づいたサンプルを次々に発生し，与えられた熱力学状態のもとで系のポテンシャルエネルギーと圧力の平均値を計算するプログラムを考える．

##### Import library

In [1]:
%matplotlib inline
import numpy as np            
import matplotlib.pyplot as plt
from scipy import linalg as la
import sys

##### Input/Output simulation parameters

In [2]:
#Simulatiopn condition
N=108        #粒子数 N
DENS=0.70    #密度 \rho
TEMP=1.0     #温度 T
#Input parameters
NSTEP=55000  #トータルモンテカルロステップ数
NEQUIL=5000  #平衡化のためのステップ数（始めのこの部分は平均操作に含まない）
IPRINT=1000  #中間データの出力間隔
IRATIO=1000  #最大変位距離の見直し間隔（新しい座標のアクセプト率が0.5以上なら小さく、以下なら大きくする）
RCUT=2.0     #相互作用の打ち切り距離（単位：σ）
RMIN=0.85    #初期座標作成のための粒子のコア直径（単位：σ）
DRMAX=0.1    #最大変位距離の初期値（単位：σ）

BETA=1.0/TEMP
L=(N/DENS)**(1/3)
if RCUT >= 0.50*L:
    RCUT=0.50*L

#write input parameter
print(" NUMBER OF PARTCLES                  =%10d"%N)
print(" NUMBER OF STEPS                     =%10d"%NSTEP)
print(" NUMBER OF STEPS FOR EQUILIBRATION   =%10d"%NEQUIL)
print(" OUTPUT FREQUENCY                    =%10d"%IPRINT)
print(" RATIO UPDATE FREQUENCY              =%10d"%IRATIO)
print(" TEMPERATURE                         =%10.4f"%TEMP)
print(" DENSITY                             =%10.4f"%DENS)
print(" POTENTIAL CUTOFF                    =%10.4f"%RCUT)

 NUMBER OF PARTCLES                  =       108
 NUMBER OF STEPS                     =     55000
 NUMBER OF STEPS FOR EQUILIBRATION   =      5000
 OUTPUT FREQUENCY                    =      1000
 RATIO UPDATE FREQUENCY              =      1000
 TEMPERATURE                         =    1.0000
 DENSITY                             =    0.7000
 POTENTIAL CUTOFF                    =    2.0000


###### Define functions


- SUMUP ( RCUT, L, V, W )

 - このサブルーチンは，一辺の長さがLのはこの中で，打ち切り距離RCUT以内にあるすべての粒子対のポテンシャルエネルギーVとビリアルWを計算する．
 - 粒子の座標RX, RY, RZはLで規格化してあるので[-0.5:0.5]の範囲にある．
 - 粒子Iから見てJとの[XYZ]座標の差が0.5を超えるか-0.5以下の場合，周期境界条件によってさらに近い距離に別のセルに属するJのミラーイメージが存在する．

- ENERGY ( RXI, RYI, RZI, I, RCUT, L, V, W )

 - このサブルーチンは，座標[RXI, RYI, RZI]にある粒子Iから見て，打ち切り距離RCUT以内にあるその他の粒子のポテンシャルエネルギーVとビリアルWを計算する．

In [3]:
#define SUMUP
def  SUMUP(RCUT, L, RX, RY, RZ): 
    RCUTSQ = (RCUT / L)**2.0
    SIGSQ = L**(-2.0)
    VW_V = 0.0
    VW_W = 0.0
    #LOOP OVER ALL THE PAIRS IN THE LIQUID
    for I in range(N-1):
        RXI = RX[I]
        RYI = RY[I]
        RZI = RZ[I]
        for J in range(I+1,N):
            RXIJ = RXI - RX[J] #粒子IとJのX座標の差
            RYIJ = RYI - RY[J] #粒子IとJのY座標の差
            RZIJ = RZI - RZ[J] #粒子IとJのZ座標の差
            #MINIMUM IMAGE THE PAIR SEPARATIONS #以下で周期境界条件を考慮
            RXIJ -= np.floor(RXIJ + 0.5) #Iの最も近くにいるJのミラーとのX座標の差
            RYIJ -= np.floor(RYIJ + 0.5) #Iの最も近くにいるJのミラーとのY座標の差
            RZIJ -= np.floor(RZIJ + 0.5) #Iの最も近くにいるJのミラーとのZ座標の差
            RIJSQ = RXIJ*RXIJ + RYIJ*RYIJ + RZIJ*RZIJ # 粒子IとJの距離^2
            if RIJSQ < RCUTSQ: #距離^2がRCUT^2より小さい場合だけ計算
                SR2 = SIGSQ / RIJSQ
                SR6 = SR2 * SR2 * SR2
                VIJ = SR6 * (SR6 - 1.0) #IJ 間のポテンシャルエネルギーの計算
                WIJ = SR6 * (SR6 - 0.5) #IJ 間のビリアルの計算
                VW_V += VIJ #全ポテンシャルエネルギーの積算
                VW_W += WIJ #全ビリアルの積算
    VW_V *= 4.0
    VW_W *= 48.0
    return(VW_V, VW_W) 

#define ENERGY
def ENERGY(RXI, RYI, RZI, I, RCUT, L, RX, RY, RZ):
    RCUTSQ=(RCUT/L)**2
    SIGSQ=L**(-2)
    VW_V=0.0
    VW_W=0.0
    for J in range(N):
        if not I ==J:
            RXIJ = RXI - RX[J]
            RYIJ = RYI - RY[J]
            RZIJ = RZI - RZ[J]
            RXIJ -= np.floor(RXIJ + 0.5)
            RYIJ -= np.floor(RYIJ + 0.5)
            RZIJ -= np.floor(RZIJ + 0.5)
            RIJSQ = RXIJ*RXIJ + RYIJ*RYIJ + RZIJ*RZIJ
            if RIJSQ < RCUTSQ:
                SR2 = SIGSQ / RIJSQ
                SR6 = SR2 * SR2 * SR2
                VIJ = SR6 * (SR6 - 1.0)
                WIJ = SR6 * (SR6 - 0.5)
                VW_V += VIJ
                VW_W += WIJ
    VW_V *= 4.0
    VW_W *= 48.0
    return(VW_V, VW_W) 

###### Create random initial configuration

- ランダムに粒子Iの初期座標を発生させる．
- すでに作成した全ての粒子　<I　について粒子Iとの距離を計算し，RMIN以下なら粒子Iの初期座標を発生し直す．
- これを繰り返して，全ての粒子がRMIN以上離れた初期配置を作成する．

In [4]:
#RANDOM INITIAL CONFIGURATION 
RX = np.zeros(N)
RY = np.zeros(N)
RZ = np.zeros(N)
np.random.seed(0)
for I in range(N):
    OL=1
    while OL == 1:
        OL=0
        RX[I]=np.random.rand()-0.50
        RY[I]=np.random.rand()-0.50
        RZ[I]=np.random.rand()-0.50
        for J in range(I):
            sys.stdout.write("\rI =%8d"%I+"/ %8d"%N+",  J =%8d"%J)
            sys.stdout.flush()
            DX=RX[I]-RX[J]
            DY=RY[I]-RY[J]
            DZ=RZ[I]-RZ[J]
            DX -= np.floor(DX+0.50)
            DY -= np.floor(DY+0.50)
            DZ -= np.floor(DZ+0.50)
            DR=np.sqrt(DX*DX+DY*DY+DZ*DZ)
            if DR*L <= RMIN:
                OL=1
                break

#CALCULATE LONG RANGE CORRECTIONS FOR V AND W
#SPECIFIC TO THE LENNARD JONES FLUID
SR3=(1/RCUT)**3
SR9=(SR3)**3
VLRC12=8.0*np.pi*DENS*float(N)*SR9/9.0
VLRC6=-8.0*np.pi*DENS*float(N)*SR3/3.0
VLRC=VLRC12+VLRC6
WLRC12=12.0*VLRC12
WLRC6=6.0*VLRC6
WLRC=WLRC12+WLRC6

#CALCULATE INITIAL ENERGY 
VW_V, VW_W = SUMUP(RCUT, L, RX, RY, RZ)
VS = (VW_V + VLRC)/float(N)
WS = (VW_W + WLRC)/float(N)
PS = DENS * TEMP+(VW_W + WLRC)/3.0/(L**3)
print("\n INITIAL V   =    %16.8e"%VS)
print(" INITIAL W   =    %16.8e"%WS)
print(" INITIAL P   =    %16.8e"%PS)

I =      59/      108,  J =      14

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =      87/      108,  J =       3

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



I =     101/      108,  J =      18

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



##### Main MC routine with Metropolis method

- N個の粒子の中からランダムに粒子Iを選択
    　
- 粒子Iの現在の座標について，他の粒子との相互作用エネルギー，ビリアルを計算

- 粒子Iをその近傍の空間に均一な確率で移動

- 粒子Iの新しい座標について，他の粒子との相互作用エネルギー，ビリアルを計算

- メトロポリスの方法にしたがって

 - 新しい座標のエネルギーのほうが小さければ確率１で新しい座標を採用する

 - 新しい座標のエネルギーのほうが大きければ、新しい一様乱数を振って確率 $\exp(-\beta \Delta U)$ で新しい座標を採用する 

 - 上記以外はもとの座標に戻す

- 操作後の物理量を平均の計算に反映する

In [5]:
#LOOPS OVER ALL CYCLES AND ALL MOLECULES  
for STEP in range(1,NSTEP+1):
    if STEP == 1 or STEP == NEQUIL+1:
        ACV     = 0.0
        ACVSQ   = 0.0
        ACP     = 0.0
        ACPSQ   = 0.0
        FLV     = 0.0
        FLP     = 0.0
        ACM     = 0.0
        ACATMA  = 0.0
    #CHOOSE ONE ATOM RANDOMLY
    I = int((float(N) - 0.000001) * np.random.rand())
    RXIOLD = RX[I]
    RYIOLD = RY[I]
    RZIOLD = RZ[I] 
    #CALCULATE THE ENERGY OF I IN THE OLD COFIGURATION 
    VWOLD_V, VWOLD_W = ENERGY(RXIOLD, RYIOLD, RZIOLD, I, RCUT, L, RX, RY, RZ)
    #MOVE I AND PICKUP THE CENTRAL IMAGE
    RXINEW = RXIOLD + (2.0 * np.random.rand() - 1.0) * DRMAX/L
    RYINEW = RYIOLD + (2.0 * np.random.rand() - 1.0) * DRMAX/L
    RZINEW = RZIOLD + (2.0 * np.random.rand() - 1.0) * DRMAX/L
    RXINEW -= np.floor(RXINEW + 0.5)
    RYINEW -= np.floor(RYINEW + 0.5)
    RZINEW -= np.floor(RZINEW + 0.5)
    #CALCULATE THE ENERGY OF I IN THE NEW COFIGURATION  */
    VWNEW_V, VWNEW_W = ENERGY(RXINEW, RYINEW, RZINEW, I, RCUT, L, RX, RY, RZ)
    #CHECK FOR ACCEPTANCE
    DELTV = VWNEW_V  - VWOLD_V
    DELTW = VWNEW_W - VWOLD_W
    DELTVB = BETA * DELTV
    if (DELTV <= 0.0) or (np.exp(-DELTVB) > np.random.rand()):
        VW_V += DELTV
        VW_W += DELTW
        RX[I] = RXINEW
        RY[I] = RYINEW
        RZ[I] = RZINEW
        ACATMA += 1.0
    ACM += 1.0
    #CALCULATE INSTANTANEOUS VALUES
    VN=(VW_V + VLRC)/float(N)
    PRES = DENS * TEMP + (VW_W + WLRC) / 3.0 / (L**3)
    #ACCUMULATE AVERAGES
    ACV += VN
    ACP += PRES
    ACVSQ += VN * VN
    ACPSQ += PRES * PRES
    #PERFORM PERIODIC OPERATIONS
    #ADJUST MAXIMUM DISPLACEMENT
    if (STEP%IRATIO) == 0:
        RATIO=ACATMA / float(IRATIO)
        if (RATIO > 0.50):
            DRMAX *=1.05
        else:
            DRMAX *=0.95
        ACATMA = 0.0
    #WRITE OUT RUNTIME INFORMATION
    if (STEP%IPRINT == 0):
        sys.stdout.write("\rSTEP =%8d"%STEP+"/ %8d"%NSTEP+",  AR =%12.6f"%RATIO+",  E_p =%16.8e"%VN+",  P =%16.8e"%PRES)
        sys.stdout.flush()

STEP =   55000/    55000,  AR =    0.517000,  E_p = -4.78945335e+00,  P =  1.02425389e-01

##### Output average values

In [6]:
#CHECKS FINAL VALUE OF THE POTENTIAL ENERGY IS CONSISTENT
VWEND_V, VWEND_W = SUMUP(RCUT, L, RX, RY, RZ)
if np.fabs((VWEND_V - VW_V)/ VWEND_V) > 1.0E-03:
    print(" PROBLEM WITH ENERGY")
    print(" VEND = %20.6e"%VWEND_V)
    print(" V    = %20.6e"%VW_V)
#CALCULATE AND WRITE OUT RUNNING AVERAGES
AVV = ACV / ACM
ACVSQ = (ACVSQ / ACM) - AVV * AVV
AVP = ACP / ACM
ACPSQ = (ACPSQ / ACM) - AVP * AVP
if(ACVSQ > 0.0):
    FLV = np.sqrt(ACVSQ)
if(ACPSQ > 0.0):
    FLP = np.sqrt(ACPSQ)
print("TEMPERATURE  = %10.4f"%TEMP)
print("DENSITY      = %10.4f"%DENS)
print("AVERAGES OF")
print(" POTENTIAL E = %10.6f"%AVV)
print(" PRESSURE    = %10.6f"%AVP)
print("FLUCTUATIONS IN")
print(" POTENTIAL E = %10.6f"%FLV)
print(" PPRESSURE   = %10.6f"%FLP)  

TEMPERATURE  =     1.0000
DENSITY      =     0.7000
AVERAGES OF
 POTENTIAL E =  -4.826760
 PRESSURE    =   0.160137
FLUCTUATIONS IN
 POTENTIAL E =   0.076879
 PPRESSURE   =   0.335092


## 課題

### 1.
- 上の説明を参考にしながらサンプルプログラムをよく読み，内容を理解せよ．

### 2.
- 温度（単位：$\epsilon$）を４種類（$T=0.5, 1.0, 2.0, 4.0$），密度（単位：数$/\sigma^3$）を５種類（$\rho=0.1, 0.2, 0.4, 0.6, 0.8, 1.0$）の全組み合わせ（合計２０組）の状態についてモンテカルロシミュレーションを行い，圧力のカノニカル平均値を求め，密度－圧力の等温線４本をグラフ化せよ．

### 3.
- 課題 2.の等温線の特徴を考察せよ．データが足りなければシミュレーションを追加して適宜補うこと．
- 考察のポイント
 - 低温と高温で圧力の密度依存性にどのような違いがあるか
 - 低温での圧力等温線の挙動は物理的にどのような現象を反映しているか
 - なぜ大きな負の圧力が実現されるのか（現実の実験ではどうなるべきか？）
 - 理想気体やファンデルワールスの状態方程式（＝平均場理論）との比較
 - マクスウェルの等面積則（体積－圧力のプロット）と気体液体の共存
 - 臨界点のおおざっぱな見積り
        　

